<a href="https://colab.research.google.com/github/hatopopvr/MyBeatSaberAnalytics/blob/main/MyBeatSaberAnalytics.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Readme

### 概要
BeatSaberのScoreSaberの情報を取得し、Rank譜面Clearの進捗状況や、Play傾向を散布図で分析するツールです。

本ツールは [Satoさん](https://twitter.com/zitasato) の [MyBeatSaberScore](https://github.com/tkns3/MyBeatSaberScore/) に影響を受け、クリア進捗やスコア傾向をグラフ等で可視化するために作成しました。  本ツールには未クリア譜面の詳細検索や未クリア譜面のプレイリスト作成機能などは含まれません。

### 使用方法

以下ツイートの動画に使い方まとめていますので、参照ください。

<blockquote class="twitter-tweet"><p lang="ja" dir="ltr">BeatSaberのScoreSaberのデータを使ってRank譜面のクリア進捗とか可視化するツール<br>概ね作りたかった機能が作り終わったので公開↓<a href="https://t.co/Roifdz8jvU">https://t.co/Roifdz8jvU</a><br><br>基本自分用かつサバ運用費や環境構築を割愛するとか諸々の都合でGoogle Colabで作ってるので使い方は以下動画参考。 <a href="https://t.co/k4WfVcpJhd">pic.twitter.com/k4WfVcpJhd</a></p>&mdash; はとぽぷ3.0 (@hatopop_vr) <a href="https://twitter.com/hatopop_vr/status/1516453029394149376?ref_src=twsrc%5Etfw">April 19, 2022</a></blockquote> <script async src="https://platform.twitter.com/widgets.js" charset="utf-8"></script>

本notebookをGoogle Colobで起動してください。
入力情報のフォームに必要事項を入力し、ランタイムでセルを実行してください。
セルを実行していただくと、Google Driveにマウントし、曲情報やPlay情報などをGoogle Driveの指定フォルダに保存します。
プレイ情報と曲情報の取得・解析には時間がかかります。

Rank譜面のClearの進捗状況や、SS/S/AなどのScoreのランクの状況を可視化できます。

<img src="https://pbs.twimg.com/media/FPBJ8_xacAU9rNA?format=jpg" />

条件を選択し散布図で分析できます。

<img src="https://pbs.twimg.com/media/FO8HJb1agAcVvn5?format=jpg" />


### 使用データ
本ツールは以下のデータを利用しています。
- ScoreSaberのPublic API - [doc](https://docs.scoresaber.com/)  
　Player情報 - https://scoresaber.com/api/player/{player_id}/full  
　Score情報 - https://scoresaber.com/api/player/{player_id}/scores?sort=recent&page={page}  
- 画像データ  
　Player画像 - https://cdn.scoresaber.com/avatars/{player_id}.jpg  
　Cover画像 - https://cdn.scoresaber.com/covers/{hash}.png  
- 曲情報  
  暫定的ですがandruzzzhkaさんがgithubで公開している[
BeatSaberScrappedData](https://github.com/andruzzzhka/BeatSaberScrappedData) を利用しています。
- Rank譜面除外リスト  
  [Rank譜面除外リスト](https://github.com/hatopopvr/ScoreSaberRankedExcludedMap)を手動作成し、強制的に除外し、[ScoreSaberのLeaderboard](https://scoresaber.com/leaderboards?page=1&verified=0&ranked=1&qualified=0&minStar=0&maxStar=20&category=1&sort=0)とのRanked譜面数と合わせる事に利用しています。この処置は暫定的です。
- nps、upvoteratio、曲のPreviewなどのBeatSaverのデータ  
らっきょさん([@rakkyo150](https://twitter.com/rakkyo150))がgithubで公開している
[RankedMapData](https://github.com/rakkyo150/RankedMapData)を利用しています。

### 使用ライブラリ

本ツールは多数のOSSのLibraryに依存しています。
使用項目については Libraryの取得 を参照願います。

### 問い合わせ先

twitter:[@hatopop_vr](https://twitter.com/hatopop_vr)

### 使用ライブラリ

In [ ]:
!pip install GitPython
!pip install -U hiplot

     |████████████████████████████████| 181 kB 4.9 MB/s 
     |████████████████████████████████| 63 kB 1.4 MB/s 
     |████████████████████████████████| 862 kB 5.3 MB/s 
     |████████████████████████████████| 793 kB 25.0 MB/s 
     |████████████████████████████████| 381 kB 51.0 MB/s 
     |████████████████████████████████| 357 kB 12.0 MB/s 
  Attempting uninstall: prompt-toolkit
    Found existing installation: prompt-toolkit 1.0.18
    Uninstalling prompt-toolkit-1.0.18:
      Successfully uninstalled prompt-toolkit-1.0.18
  Attempting uninstall: ipython
    Found existing installation: ipython 5.5.0
    Uninstalling ipython-5.5.0:
      Successfully uninstalled ipython-5.5.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
jupyter-console 5.2.0 requires prompt-toolkit<2.0.0,>=1.0.0, but you have prompt-toolkit 3.0.29 which is incompatible.
google-colab 1.0.0 

In [ ]:
#@title Libraryの取得
import warnings
warnings.filterwarnings("ignore")
import os
import shutil
import pandas as pd
from pandas import json_normalize
import json
from datetime import datetime
from dateutil import tz
#import matplotlib
#import seaborn as sns
import plotly.express as px
from ipywidgets import interact, Select, BoundedIntText, IntSlider, ToggleButtons, Layout, HBox, VBox, AppLayout
import time
from tqdm import tqdm
import requests
import math
import git
import gc
import hiplot as hip
from IPython.display import HTML, Javascript
from google.colab import drive, files


# 入力情報

## 入力変数
- player_id: ScoreSaberのPlayerIDです。  
- google_drive_mount_path: GoogleDriveのマウント先です。変更不要。  
- google_drive_dir_path: GoogleDrive内の保存先です。必要に応じて変更してください。  
- saved_song_list_is_enable:解析済の曲情報を使用するか。☑で使用。※新規取得は数十分要。
- saved_player_score_is_enable:
解析済のプレイ情報を使用するか。☑で使用。※処理時間は総PlayCountに依存。  
- acc_recalq_override_is_enable: MaxScore,Accを再計算した値をMaxScore,Accに上書きするか。☑で使用。
- ss_plus_is_enable:
AccRank区分にSS+を使用するか。☑で使用。  
- ss_plus_val:
SS+の設定値です。必要に応じて変更ください。範囲は91-99。  
- latest:直近の成果として扱う対象の日数です。0は日本時間で今日と同じ日付。例)今日が5/9で1なら5/8以降のデータ。   
 ※名称がlatestだったりRecentだったり混在してしまっていますが許してください。


In [ ]:
#@title 変数概要を参照し、以下のデータを入力してください。 { display-mode: "form" }
player_id =  76561198412839195#@param {type:"number"}
google_drive_mount_path = "/content/drive" #@param {type:"string"}
google_drive_dir_path = "/MyDrive/MyBeatSaberAnalysis/data" #@param {type:"string"}
saved_song_list_is_enable = True #@param {type:"boolean"}
saved_player_score_is_enable = False #@param {type:"boolean"}
acc_recalq_override_is_enable = True #@param {type:"boolean"}
ss_plus_is_enable = True #@param {type:"boolean"}
ss_plus_val = 95 #@param {type:"slider", min:91, max:99, step:1}
latest =  0#@param {type:"integer"}

In [ ]:
#@title Timezone UTC->日本時間+9:00での実行日時の取得(tz_ja)
tz_ja = pd.Timestamp(datetime.now()).tz_localize('UTC').tz_convert('Asia/Tokyo')
#today_tz_ja = datetime_now_tz_ja.strftime("%Y.%m.%d")
print("取得日時:{}".format(tz_ja))

取得日時:2022-05-11 23:16:59.594803+09:00


In [ ]:
#@title Google Driveのマウント
drive.mount(google_drive_mount_path)

Mounted at /content/drive


In [ ]:
#@title その他設定値
# データ元のURL
## song_data_zip_git_url: ScoreSaberの全曲情報のzip(json)のURLです。変更なければそのままで。 
song_data_zip_git_url = "https://github.com/andruzzzhka/BeatSaberScrappedData.git"
## ranked_excluded_data_git_url: ScoreSaberのRank譜面除外リスト(csv)のURLです。暫定的処置。 
ranked_excluded_data_git_url = "https://github.com/hatopopvr/ScoreSaberRankedExcludedMaps.git"
## rankedmapdata_url: BeatSaverデータのcsvのURLです。らっきょさんデータ。 
rankedmapdata_url = 'https://api.github.com/repos/rakkyo150/RankedMapData/releases'
# google drive内のdata置き場親フォルダ
data_path = r"{}{}".format(google_drive_mount_path, google_drive_dir_path)
# player情報の親フォルダ(data_pathの子フォルダ)
player_path = r"{}/players_data/{}".format(data_path, player_id)
## playerinfoの保存先
#player_info_path = r"{}/player_info_{}.csv".format(data_path, player_id)
player_info_path = r"{}/player_info_{}.csv".format(player_path, player_id)
## playerのscore関連保存先
# player_score_path = r"{}/scores_full_{}.csv".format(data_path, player_id)
# player_ranked_path = r"{}/scores_ranked_{}.csv".format(data_path, player_id)
player_score_path = r"{}/scores_full_{}.csv".format(player_path, player_id)
player_ranked_path = r"{}/scores_ranked_{}.csv".format(player_path, player_id)
## 曲情報の保存関連
song_clone_path = r"/content/BeatSaberScrappedData"
song_zip_path = r"{}/combinedScrappedData.zip".format(song_clone_path)
song_json_path = r"{}/combinedScrappedData.json".format(data_path)
## 曲情報の保存先
song_list_path = r"{}/song_list_full.csv".format(data_path)
song_ranked_path = r"{}/song_ranked.csv".format(data_path)
# song_playlist_path = r"{}/playlist_{}.json".format(data_path, datetime.now().strftime("%Y%m%d"))
# ランク除外関連パス
ranked_excluded_clone_dir_path = r"/content/ScoreSaberRankedExcludedMaps"
ranked_excluded_clone_csv_path = r"{}/RankedExcludedMaps.csv".format(ranked_excluded_clone_dir_path)
ranked_excluded_csv_path = r"{}/RankedExcludedMaps.csv".format(data_path)
# levelclearランク除外関連パス
#level_cleared_path = r"{}/level_cleared_{}.csv".format(data_path, player_id)
level_cleared_path = r"{}/level_cleared_{}.csv".format(player_path, player_id)

# playlistの保存
song_playlist_path = r"{}/playlists".format(data_path)
song_worst_playlist_path = r"{}/worst_playlist_{}.json".format(song_playlist_path, tz_ja.strftime("%Y%m%d"))
song_top_playlist_path = r"{}/top_playlist_{}.json".format(song_playlist_path, tz_ja.strftime("%Y%m%d"))

# SS_plus設定値
ss_plus = "SS+{}".format(ss_plus_val)
ss_plus_rate = "SS+{}-Rate".format(ss_plus_val)
# その他 colab表示など設定
pd.options.display.precision = 2
pd.set_option("display.max_rows", None)
pd.set_option("display.max_columns", None)
page_count=8 #ScoreSaberの1ページあたりのページ数
image_size=70 #カバー,プロファイル画像のサイズ単位px

# 出力最大高さ
def resize_colab_cell():
    display(Javascript('google.colab.output.setIframeHeight(0, true, {maxHeight: 5000})'))
get_ipython().events.register('pre_run_cell', resize_colab_cell)

In [ ]:
#@title 各種フォルダの作成
# 各種パスのディレクトリ作成
## データ大元のフォルダ作成
if os.path.exists(data_path) == False:
    print('MyBeatSaberAnalytics用のデータ格納フォルダをGoogle Driveに新規作成します。')
    print('データ格納フォルダ:{}'.format(data_path))     
    os.makedirs(data_path, exist_ok=True)
    print('作成が完了しました。')         

## データ大元のフォルダ作成
if os.path.exists(player_path) == False:
    old_player_info_path = r"{}/player_info_{}.csv".format(data_path, player_id)
    print('PlayerID:{}用のデータ格納フォルダを新規作成します。'.format(player_id))
    print('playerフォルダ:{}'.format(player_path))     
    print('作成が完了しました。')         
    os.makedirs(player_path, exist_ok=True)
    if os.path.isfile(old_player_info_path):
        print('データ引継ぎのため、player_infoｂのcsvファイルを上記フォルダに移動させます。')
        print('移動前:{}'.format(old_player_info_path))
        print('移動後:{}'.format(player_info_path))
        shutil.move(old_player_info_path, player_info_path)
        print('移動が完了しました。')

## プレイヤー用のフォルダ作成
if os.path.exists(song_playlist_path) == False:
    print('Playlist格納用のフォルダを新規作成します。')
    print('Playlist格納フォルダ:{}'.format(song_playlist_path))     
    os.makedirs(song_playlist_path, exist_ok=True)
    print('作成が完了しました。')         

<IPython.core.display.Javascript object>

In [ ]:
#@title 列情報の設定
# Player Infoの記録用列 (TotalFC, RankedFCは別途結合)
cols_info =[
    "Pic"
    ,"name"
    ,"country"
    ,"pp"
    ,"rank"
    ,"countryRank"
    ,"role"
    ,"TotalScore"
    ,"RankedScore"
    ,"AveRankedAcc"
    ,"TotalPlay"
    ,"RankedPlay"
    ,"ReplayWatched"
    ,"ScoreDate"
    ,"TotalFC"
    ,"RankedFC"
]

# Player Infoの表示用列 (TotalFC, RankedFCは別途結合)
cols_info_sort =[
    "Pic"
    ,"name"
    ,"country"
    ,"pp"
    ,"rank"
    ,"countryRank"
    ,"role"
    ,"TotalScore"
    ,"RankedScore"
    ,"AveRankedAcc"
    ,"TotalPlay"
    ,"RankedPlay"
    ,"TotalFC"
    ,"RankedFC"
    ,"ReplayWatched"
    ,"ScoreDate"
]

# summary用列
cols_summary =[
    "rank"
    ,"countryRank"
    ,"pp"
    ,"AveRankedAcc"
    ,"TotalPlay"
    ,"RankedPlay"
]

# SongList抜粋用列
cols_song =[
    "Cover"
    ,"Song"
    ,"Level"
    ,"LevelStr"
    ,"Stars"
    # ,"maxPP"
    # ,"maxScore"
    ,"Difficulty"
    # ,"Play"
    # ,"DailyPlay"
    ,"CreatedDateJa"
    ,"RankDateJa"
    ,"Bombs"
    ,"Notes"
    ,"Obstacles"
    ,"Njs"
    ,"NjsOffset"
    ,"Bpm"
    ,"Upvotes"
    #,"Downvotes"
    ,"Duration"
    ,"Ranked"
]

# Rank譜面除外リスト結合用列
cols_excluded = [
                 'Hash',
                 'Difficulty',
                 'RankedExcluded'
                 ]

# Score用列
cols_score =[
    "Cover"
    ,"Song"
    ,"Level"
    ,"Stars"
    ,"Acc"
    ,"AccRank"
    ,"FC"
    ,"Rank"
    ,"PP"
    ,"Miss"
    ,"Bad"
    ,"Combo"
    ,"Score"
    #,"Mode"
    ,"Difficulty"
    ,"Play"
    ,"DailyPlay"
    ,"Bpm"
    ,"Duration"
    ,"Notes"
    ,'Nps'
    ,"Njs"
    ,"Bombs"
    ,"Obstacles"
    ,"NjsOffset"
    ,'Upvotesratio' 
    ,"Upvotes"
    ,"Downvotes"
    ,"Ranked"
    ,"Days"
    ,"Months"
    ,"Tags"
    ,"Preview"
 ]

# Acc再計算用列
cols_recalq = [
    'Hash',
    'Cover',
    'SongName',
    'Difficulty', 'Stars', 
    'Ranked', 
    'Notes', 
    'Acc', 
    'AccRecalq', 
    'AccDiff',
    'AccRank', 
    'AccRankRecalq', 
    'MaxScore',
    'MaxScoreRecalq',
    'MaxScoreDiff',
    'Score', 
    'Miss', 
    'Combo',
    'RankDateJa',
    'CreatedDateJa', 
    'Preview'
]

# ScatterPlot用X-Y軸列
cols_xy = [
    "Stars"
    ,"Level"
    ,"Acc"
    ,"Rank"
    ,"PP"
    ,"Miss"
    ,"Bad"
    ,"Combo"
    ,"Score"
    ,"Play"
    ,"DailyPlay"
    ,"Days"
    ,"Months"
    ,"Bpm"
    ,"Duration"
    ,"Notes"
    ,'Nps'
    ,"Njs"
    ,"Bombs"
    ,"Obstacles"
    ,"NjsOffset"
    ,'Upvotesratio'
    ,"Upvotes"
    ,"Downvotes"
]

# RankedMap(BeatSaver)結合用列
cols_rankedmap = ['Hash', 
                  'Difficulty', 
                  'Upvotesratio',
                  'Nps', 
                  'Tags', 'Preview'
]

# ScatterPlot用カテゴリ
cols_cate = [
    "LevelStr"
    ,"Days"
    ,"DaysStr"
    ,"Months"
    ,"MonthsStr"
    ,"LatestStr"
    ,"Acc"
    ,"AccRank"
    ,"FC"
]

# Worst-Top ScatterPlot用カテゴリ
cols_cate_wt = [
    "WorstTop"
    ,"LevelStr"
    ,"Days"
    ,"DaysStr"
    ,"Months"
    ,"MonthsStr"
    ,"LatestStr"
    ,"Acc"
    ,"AccRank"
    ,"FC"
]

<IPython.core.display.Javascript object>

# データの取得

## Get Player Info (df_info)

In [ ]:
#@title Player情報の取得
url = r"https://scoresaber.com/api/player/{}/full".format(player_id)
response = requests.get(url)
res_data = response.json()
df_info = json_normalize(res_data)

df_info["Pic"] = '<img src="'+df_info["profilePicture"]+'"/>'
df_info["TotalScore"] = df_info["scoreStats.totalScore"]
df_info["RankedScore"] = df_info["scoreStats.totalRankedScore"]
df_info["AveRankedAcc"] = df_info["scoreStats.averageRankedAccuracy"]
df_info["TotalPlay"] = df_info["scoreStats.totalPlayCount"]
df_info["RankedPlay"] = df_info["scoreStats.rankedPlayCount"]
df_info["ReplayWatched"] = df_info["scoreStats.replaysWatched"]
df_info["ScoreDate"] = datetime.now().strftime("%Y/%m/%d %H:%M:%S")

PlayCount = df_info["TotalPlay"][0]
RangeCount = math.ceil(PlayCount / page_count) + 1

# if os.path.exists(player_info_path):
#     df_info[cols_info].to_csv(player_info_path, mode="a", index=None, header=False)
# else:
#     df_info[cols_info].to_csv(player_info_path, index=None)

# df_infos = pd.read_csv(player_info_path)
# df_infos["ScoreDate"] = pd.to_datetime(df_infos["ScoreDate"])

print("Player:{}, Play数:{}, Page数:{}".format(df_info["name"][0], PlayCount, RangeCount))

<IPython.core.display.Javascript object>

Player:hatopop, Play数:1639, Page数:206


## Get Song List (df_songs, df_ranked_songs)

In [ ]:
#@title Song Listを取得し展開(最新取得は30分程度かかる可能性あり)
if saved_song_list_is_enable and os.path.exists(song_list_path):
    df_songs = pd.read_csv(song_list_path)
    df_ranked_songs = df_songs[
                    (1==1)
                    &(df_songs['Ranked'])
                    &(df_songs['Mode'] == 'Standard')
                    ].drop('index', axis=1).drop_duplicates()

else:
    # GithubからZipのダウンロード
    if os.path.exists(song_clone_path):
        shutil.rmtree(song_clone_path)

    git.Git().clone(song_data_zip_git_url)

    # Zipの解凍
    shutil.unpack_archive(song_zip_path, data_path)

    json_open = open(song_json_path,"r", encoding="utf-8")
    json_load = json.load(json_open)
    _df_songs_from_json = json_normalize(json_load)

    cnt=0

    _df_song_from_json = _df_songs_from_json.loc[0]

    # jsonの入れ子のDiffsの内容を展開
    _df_song = json_normalize(_df_song_from_json["Diffs"])
    _df_song["Bsr"]=_df_song_from_json["Key"]
    _df_song["Hash"]=_df_song_from_json["Hash"]
    _df_song["SongName"]=_df_song_from_json["SongName"]
    _df_song["SongSub"]=_df_song_from_json["SongSubName"]
    _df_song["SongAuthor"]=_df_song_from_json["SongAuthorName"]
    _df_song["LevelAuthor"]=_df_song_from_json["LevelAuthorName"]
    #_df_song["Chars"]=_df_song_from_json["Chars"][0]
    _df_song["Uploaded"]=_df_song_from_json["Uploaded"]
    _df_song["Uploader"]=_df_song_from_json["Uploader"]
    _df_song["Bpm"]=_df_song_from_json["Bpm"]
    _df_song["Upvotes"]=_df_song_from_json["Upvotes"]
    _df_song["Downvotes"]=_df_song_from_json["Downvotes"]
    _df_song["Duration"]=_df_song_from_json["Duration"]

    # headerの作成
    df_songs = _df_song

    for idx in tqdm(range(len(_df_songs_from_json))):

        if cnt == 0:
            cnt+=1
            pass
        cnt+=1
        # jsonの入れ子のDiffsの内容を展開
        _df_song = json_normalize(_df_songs_from_json.loc[idx]["Diffs"])
        _df_song["Bsr"]=_df_songs_from_json.loc[idx]["Key"]
        _df_song["Hash"]=_df_songs_from_json.loc[idx]["Hash"]
        _df_song["SongName"]=_df_songs_from_json.loc[idx]["SongName"]
        _df_song["SongSub"]=_df_songs_from_json.loc[idx]["SongSubName"]
        _df_song["SongAuthor"]=_df_songs_from_json.loc[idx]["SongAuthorName"]
        _df_song["LevelAuthor"]=_df_songs_from_json.loc[idx]["LevelAuthorName"]
        #_df_song["Chars"]=_df_songs_from_json.loc[idx]["Chars"][0]
        _df_song["Uploaded"]=_df_songs_from_json.loc[idx]["Uploaded"]
        _df_song["Uploader"]=_df_songs_from_json.loc[idx]["Uploader"]
        _df_song["Bpm"]=_df_songs_from_json.loc[idx]["Bpm"]
        _df_song["Upvotes"]=_df_songs_from_json.loc[idx]["Upvotes"]
        _df_song["Downvotes"]=_df_songs_from_json.loc[idx]["Downvotes"]
        _df_song["Duration"]=_df_songs_from_json.loc[idx]["Duration"]
        df_songs = df_songs.append(_df_song, ignore_index=True)

    # 欲しい形に加工
    df_songs["Song"] = df_songs["SongName"] + " " + df_songs["SongSub"] + " / " + df_songs["SongAuthor"] + " [" + df_songs["LevelAuthor"] + "]"
    df_songs.rename(columns={
                            "Diff":"Difficulty",
                             "Char":"Mode"
                             }, inplace=True)
    df_songs["Level"] = df_songs["Stars"].astype("int")
    df_songs["LevelStr"] = df_songs["Level"].astype("str")
    df_songs["Hash"] = df_songs["Hash"].str.upper()
    df_songs["Cover"] = '<img src="https://cdn.scoresaber.com/covers/' + df_songs["Hash"] + '.png" style="width:{}px;"/>'.format(image_size)
    df_songs["RankDateUtc"] = pd.to_datetime(df_songs["RankedUpdateTime"])
    _df_songs_idx = df_songs.set_index("RankDateUtc")
    df_songs["RankDateJa"] = _df_songs_idx.index.tz_convert("Asia/Tokyo")
    df_songs = df_songs.set_index("RankDateJa")
    df_songs = df_songs.reset_index()
    df_songs["CreatedUtc"] = pd.to_datetime(df_songs["Uploaded"])
    _df_songs_idx = df_songs.set_index("CreatedUtc")
    df_songs["CreatedDateJa"] = _df_songs_idx.index.tz_convert("Asia/Tokyo")
    df_songs = df_songs.reset_index()
    
    # 改行コード等の除去
    for col in df_songs.columns:
        try:
            if len(df_songs[df_songs[col].str.contains("\n")][[col]]) == 0:
                continue
            else:
                df_songs[col] = df_songs[col].str.replace("\n","")
        except:
            continue

    for col in df_songs.columns:
        try:
            if len(df_songs[df_songs[col].str.contains("\r")][[col]]) == 0:
                continue
            else:
                df_songs[col] = df_songs[col].str.replace("\r","")
        except:
            continue

    # # SongListの保存
    # df_ranked_songs = df_songs[
    #                     (1==1)
    #                     &(df_songs['Ranked'])
    #                     &(df_songs['Mode'] == 'Standard')
    #                     ].drop('index', axis=1).drop_duplicates()
    # df_ranked_songs.to_csv(song_ranked_path, index=False)

    # SongListの保存
    df_songs.to_csv(song_list_path, index=False)

print("Song:{}".format(df_songs["Song"].count()))

<IPython.core.display.Javascript object>

Song:95384


In [ ]:
#@title Rank除外リスト取得し曲リストに結合とランク譜面リストの抽出 (df_ranked_songs)

# Githubからランク除外リストcsvのダウンロード
if os.path.exists(ranked_excluded_clone_dir_path):
    shutil.rmtree(ranked_excluded_clone_dir_path)

git.Git().clone(ranked_excluded_data_git_url)
shutil.copy(ranked_excluded_clone_csv_path, data_path)

df_ranked_excluded = pd.read_csv(ranked_excluded_csv_path)

df_songs = pd.merge(df_songs, df_ranked_excluded[cols_excluded], on=["Hash", "Difficulty"], how="outer", suffixes=("", "_y"))

df_ranked_songs = df_songs[
            (1==1)
            &(df_songs['Ranked']==True)
            &(df_songs['Mode'] == 'Standard')
            &(df_songs['RankedExcluded']!=True)
            ].drop('index', axis=1).drop_duplicates()

df_ranked_songs.to_csv(song_ranked_path, index=False)

print("RankedSong:{}".format(df_ranked_songs["Song"].count()))

<IPython.core.display.Javascript object>

RankedSong:2936


In [ ]:
#@title NPS、UpvoteRatio、Preview等のBeatSaverDataの取得
headers = {
    'Accept': 'application/vnd.github.v3+json',
}

response = requests.get(rankedmapdata_url, headers=headers)

data = response.json()

# 最新releaseのcsvのurl取得
url_rankmap_data = data[0]["assets"][0]["browser_download_url"]

file_name = os.path.join(data_path, os.path.basename(url_rankmap_data))
result = requests.get(url_rankmap_data, stream=True)
if result.status_code == 200:
    with open(file_name, 'wb') as file:
        result.raw.decode_content = True
        shutil.copyfileobj(result.raw, file)

df_rankmap_data = pd.read_csv(file_name)
df_rankmap_data = df_rankmap_data[[x for x in df_rankmap_data.columns if not x.startswith("Unnamed")]]
df_rankmap_data["hash"] = df_rankmap_data["hash"].str.upper()
df_rankmap_data["Preview"] = '<audio src="' + df_rankmap_data["previewUrl"] + '" preload="none" controls></audio>'

df_rankmap_data = df_rankmap_data.rename(columns=lambda x: x.capitalize())
#df_rankmap_data.drop_duplicates().head()

# df_ranked_songs_append = pd.merge(df_ranked_songs, df_rankmap_data, on=["Hash", "Difficulty"], how="outer", suffixes=("", "_y"))
# df_ranked_songs_append = df_ranked_songs_append[[x for x in df_ranked_songs_append.columns if not x.endswith("_y")]]

print("path:{},曲数:{}".format(file_name,len(df_rankmap_data["Hash"])))

<IPython.core.display.Javascript object>

path:/content/drive/MyDrive/MyBeatSaberAnalysis/data/outcome.csv,曲数:2936


## Get Player Scores (df_scores)

In [ ]:
#@title Score情報の取得
if saved_player_score_is_enable and os.path.exists(player_score_path):    
    df_scores = pd.read_csv(player_score_path)

else:
    url = r"https://scoresaber.com/api/player/{}/scores?sort=recent".format(player_id)
    response = requests.get(url)
    res_data = response.json()
    df_scores = json_normalize(res_data['playerScores'])

    for i in tqdm(range(2, RangeCount)):
        url = r"https://scoresaber.com/api/player/{}/scores?sort=recent&page={}".format(player_id, i)
        try:
            response = requests.get(url)
            res_data = response.json()
            #df2 = json_normalize(res_data['playerScores'])
            df_scores=df_scores.append(json_normalize(res_data['playerScores']), ignore_index=True)
        except:
            break

    df_scores['Song'] = df_scores['leaderboard.songName'] + " " + df_scores['leaderboard.songSubName'] + " / " + df_scores['leaderboard.songAuthorName'] + " [" + df_scores['leaderboard.levelAuthorName'] + "]"
    df_scores['SongName'] = df_scores['leaderboard.songName']
    df_scores['SongSub'] = df_scores['leaderboard.songSubName']
    df_scores['SongAuthor'] = df_scores['leaderboard.songAuthorName']
    df_scores['LevelAuthor'] = df_scores['leaderboard.levelAuthorName']
    df_scores['Hash'] = df_scores['leaderboard.songHash'].str.upper()
    df_scores['Acc'] = df_scores['score.modifiedScore'] / df_scores['leaderboard.maxScore'] * 100
    df_scores['MaxScore'] = df_scores['leaderboard.maxScore']

    def func_mode(x):
        if  x == "SoloStandard":
            return "Standard"
        else:
            return x

    df_scores['Mode'] = df_scores['leaderboard.difficulty.gameMode'].apply(func_mode)
    #df_scores['Mode'] = df_scores['leaderboard.difficulty.gameMode']
    _df_scores = df_scores['leaderboard.difficulty.difficultyRaw'].str.split('_', expand=True)
    _df_scores.columns = ['_','Difficulty', 'Mode']
    df_scores['Difficulty'] = _df_scores['Difficulty']
    df_scores['Stars'] = df_scores['leaderboard.stars']
    df_scores['Level'] = df_scores['Stars'].astype('int')
    df_scores["LevelStr"] = df_scores['Level'].astype('str')
    df_scores['Score'] = df_scores['score.modifiedScore']
    df_scores['Bad'] = df_scores['score.badCuts']
    df_scores['Miss'] = df_scores['score.missedNotes']
    df_scores['Combo'] = df_scores['score.maxCombo']
    df_scores['PP'] = df_scores['score.pp']
    df_scores['PPWeight'] = df_scores['score.pp'] * df_scores['score.weight']
    df_scores['Rank'] = df_scores['score.rank']
    df_scores['Modifiers'] = df_scores['score.modifiers']
    df_scores['Ranked'] = df_scores['leaderboard.ranked']
    df_scores['Qualified'] = df_scores['leaderboard.qualified']
    df_scores['Play'] = df_scores['leaderboard.plays']
    df_scores['DailyPlay'] = df_scores['leaderboard.dailyPlays']
    df_scores['DateUtc'] = pd.to_datetime(df_scores['score.timeSet'])
    _df_scores_idx = df_scores.set_index('DateUtc')
    df_scores['DateJa'] = _df_scores_idx.index.tz_convert('Asia/Tokyo')
    df_scores['Date'] = df_scores['DateJa'].dt.date
    df_scores['Days'] = (tz_ja.date() - df_scores['Date']).dt.days
    df_scores = df_scores.set_index('DateJa')
    #df_scores['Days'] = (pd.Timestamp(datetime.now(), tz='Asia/Tokyo') - df_scores.index).days
    #df_scores['Days'] = (pd.Timestamp(datetime.now()).tz_localize('UTC').tz_convert('Asia/Tokyo') - df_scores.index).days
    #df_scores['Days'] = (tz_ja - df_scores.index).days
    df_scores['Months'] = (df_scores['Days'] / 30).astype('int')
    df_scores['DaysStr'] = df_scores['Days'].astype('str')
    df_scores['MonthsStr'] = df_scores['Months'].astype('str')
    def func_latest(x):
        if  x <= latest:
            return 1
        else:
            return 0

    df_scores['Latest'] = df_scores['Days'].apply(func_latest)
    
    def func_score(x):
        if  x == 100:
            return "SSS"
        elif x >= ss_plus_val and ss_plus_is_enable:
            return ss_plus
        elif x >= 90:
            return "SS"
        elif x >= 80:
            return "S"
        elif x >= 65:
            return "A"
        elif x >= 50:
            return "B"
        elif x >= 35:
            return "C"
        elif x >= 20:
            return "D"
        elif x >= 0:
            return "E"
        else:
            return "-"

    df_scores['AccRank'] = df_scores['Acc'].apply(func_score)
  
    df_scores['Cover'] = '<img src="'+df_scores['leaderboard.coverImage']+'" style="width:{}px;"/>'.format(image_size)

    def func_fc(x):
        if  x:
            return "FC"
        else:
            return "-"

    df_scores['FC'] = df_scores['score.fullCombo'].apply(func_fc)

    df_scores = df_scores[[x for x in df_scores.columns if not x.startswith("score.")]]
    df_scores = df_scores[[x for x in df_scores.columns if not x.startswith("leaderboard.")]]

    # Songsの情報結合
    df_scores_org = df_scores.copy()
    df_scores = df_scores.reset_index()
    df_songs['Hash'] = df_songs['Hash'].str.upper()
    df_scores = pd.merge(df_scores, df_songs, on=["Hash", "Difficulty","Mode"], how="inner", suffixes=("", "_y"))
    df_scores = df_scores[[x for x in df_scores.columns if not x.endswith("_y")]]
    #df_scores = df_scores.set_index("DateJa")

    # RankedMap(らっきょさんのBeatSaverデータ)の情報結合
    #df_scores = df_scores.reset_index()
    df_scores = pd.merge(df_scores, df_rankmap_data[cols_rankedmap], on=["Hash", "Difficulty"], how="outer", suffixes=("", "_y"))
    df_scores = df_scores[[x for x in df_scores.columns if not x.endswith("_y")]]
    df_scores = df_scores.set_index("DateJa")
    df_scores = df_scores.drop('index', axis=1).drop_duplicates()

    #Score情報の保存
    df_scores[(df_scores['Ranked'] == True)][cols_score].sort_index(ascending=False).to_csv(player_ranked_path)
    df_scores.sort_index(ascending=False).to_csv(player_score_path.format(player_id))

print('ScoreCount:{}, LatestPlayCount:{}, RankedPlayCount:{}'.format(df_scores['Play'].count(), df_scores[(df_scores['Latest'] == 1)]['Play'].count(), df_scores[
                                    (df_scores['Ranked']==1)
                                    & (df_scores['Mode']=="Standard")]['Play'].count()))

<IPython.core.display.Javascript object>

100%|██████████| 204/204 [00:42<00:00,  4.84it/s]


ScoreCount:1632, LatestPlayCount:42, RankedPlayCount:1600


## MaxScore/Accの再計算とアンマッチの取得(df_errors)
※ScoreSaberの一部譜面ではMaxScoreの数値が間違っており、Accがゲーム内と異なった数値になっているものがあるため、再計算をする。数値が異なる件については[リンク](https://twitter.com/FaZ_Pi/status/1517153139027152897)参照  
Accは以下の計算式で得られる。  
```
Acc = Score / MaxScore * 100 % 
```  
MaxScoreは最大ノーツ数(コンボ数)を元に算出できる。

```
全ノーツ数をxとするとMaxScoreは以下で得られる。
if x >= 14: 
    MaxScore = (d) * (x - 13) + (c) * 8 + (b) * 4 + (a) 
elif x >= 6:
    MaxScore = (c) * (x - 5)+ (b) * 4 + (a) 
elif x >= 2:
    MaxScore = (b) * (x - 1) + (a)
elif x >= 1:
    MaxScore = (a)
```
各コンボ時のスコアは以下
- (a)コンボ1：倍率1 → 115 (最大1ノーツ)  
- (b)コンボ2-5：倍率2 → 115x2 (最大4ノーツ)  
- (c)コンボ6-13：倍率4 → 115x4 (最大8ノーツ)  
- (d)コンボ14-：倍率8 → 115x8 (最大全ノーツ数-13)  

In [ ]:
#@title 再計算とアンマッチの取得
def func_max_score(x):
    combo_a = 115 * 1
    combo_b = 115 * 2
    combo_c = 115 * 4
    combo_d = 115 * 8

    if  x >= 14:
        return combo_d * (x - 13) + combo_a + combo_b * 4 + combo_c * 8
    elif x >= 6:
        return combo_c * (x - 5) + combo_a + combo_b * 4
    elif x >= 2:
        return combo_b * (x - 1) + combo_a
    elif x >= 1:
        return combo_a
    else:
        return 0

df_scores['MaxScoreRecalq'] = df_scores['Notes'].apply(func_max_score)
df_scores['AccRecalq'] = df_scores['Score'] / df_scores['MaxScoreRecalq'] * 100
df_scores['AccRankRecalq'] = df_scores['AccRecalq'].apply(func_score)
df_scores['MaxScoreDiff'] = df_scores['MaxScore'].fillna(0) - df_scores['MaxScoreRecalq'].fillna(0)
df_scores['AccDiff'] = df_scores['Acc'].fillna(0) - df_scores['AccRecalq'].fillna(0)

df_errors = df_scores[
            (1==1)
            &(df_scores['Ranked'])
            &(df_scores['MaxScoreDiff'] != 0)
            ]

print('Accがゲームと異なる結果が{}件あります。'.format(len(df_errors)))

if acc_recalq_override_is_enable:
    df_scores.rename(columns={
                            "MaxScore":"MaxScoreOrg",
                             "Acc":"AccOrg",
                             "AccRank":"AccRankOrg"
                             }, inplace=True)
    df_scores.rename(columns={
                            "MaxScoreRecalq":"MaxScore",
                             "AccRecalq":"Acc",
                             "AccRankRecalq":"AccRank"
                             }, inplace=True)
    print('Accを再計算した結果を上書きしました。')

print('再計算時に抽出した結果は以下です。')

def color_negative_red(val):
    """
    Takes a scalar and returns a string with
    the css property `'color: red'` for negative
    strings, black otherwise.
    """
    color = 'red' if val < 0 else 'blue'
    return 'color: %s' % color

df_errors[cols_recalq].style.applymap(color_negative_red, subset=["AccDiff","MaxScoreDiff"]).set_precision(2)
#df_errors[cols_recalq].style.highlight_null(null_color="lightgray").set_precision(2)

<IPython.core.display.Javascript object>

Accがゲームと異なる結果が13件あります。
Accを再計算した結果を上書きしました。
再計算時に抽出した結果は以下です。


## Ranked - Calc Level Cleared Progress (df_progress) 

### データについての捕捉  

__データについての捕捉__

- 分母であるRank譜面の曲数について１  
取得した曲データから"Ranked"==True かつ "Mode"=="Standard"でユニークなデータを計上しています。  
<"Standard"のみの採用理由>  
[ScoreSaber Ranking Criteria](https://docs.google.com/document/d/1_EBmvCTHyJ5-0ox5IZgmnItVqAjaBWltWslxqSc5_-4/edit#heading=h.11dlgmbqgxsa)のRules 1.Gameplay の記述(以下)に基づいています。
> Maps must be ‘Standard’ game mode maps.   

- 分母であるRank譜面の曲数について２  
<ScoreSaberとRank譜面の曲数が一致しない問題について>  
１．の上記条件に加えて、[Rank譜面除外リスト](https://github.com/hatopopvr/ScoreSaberRankedExcludedMap)を手動作成し、強制的に除外し、Ranked譜面数の一致を図っています。[ScoreSaberのLeaderboard](https://scoresaber.com/leaderboards?page=1&verified=0&ranked=1&qualified=0&minStar=0&maxStar=20&category=1&sort=0)と照合し、2022/4/24 21:00+09:00時点全曲数が一致することを確認しましたが、将来的に乖離することが予測されます。データ取得元によって正される事が理想であり、この処置は暫定的である事を想定しています。

- クリア数 Cleared Count について  
ScoreSaberで集計される Ranked Play Count についてはNoFailでのクリアも数値に計上されますが、本ツールでは NoFail でのクリアを区別し、クリア数 Cleared Countに含みません。NoFailで進捗率100%が埋まるのはツール作成者の本意ではないためです。そのため、数値が ScoreSaberのRanked Play Countと一致しない旨をご了承ください。  

- Acc Rank SS+ について  
区分がSSでは足りないScoreSaber Rank上位者向けに SS+を追加しました。  
BeatSaber内の区分には存在しないため、有効無効は任意で[入力変数](#scrollTo=Zgpr4DqIzPth)の `ss_plus_is_enable` を有効にする事で追加されるようにしています。  
またSS+の線引きについて、ScoreSaberのカーブが従来と変わっている事や、Rank上位者でも狙いの数値が異なることが考えられるため、可変にしています。
SS+の値変更時は不便かもしれないですが、[入力変数](#scrollTo=Zgpr4DqIzPth)の `ss_plus_val` の値変更と全てのセルの実行をお願いします。※設定値の反映と[Score情報の取得](#scrollTo=bO5JFBG8fvZz)項目から再計算を行うため。  

__謝辞__

- 本ツールでの曲数計上の整合性について [HPC](https://twitter.com/HPC______)さん、[sato](https://twitter.com/zitasato)さん、[ふぁずぱい](https://twitter.com/FaZ_Pi)さんに協力頂きました。  
- SS+の設定追加について [ふぁずぱい](https://twitter.com/FaZ_Pi)さんに協力頂きました。  
感謝。

### 結合処理

In [ ]:
#@title Level別 Clear 情報の結合
df_progress = df_ranked_songs[["Level","Song"]].groupby(["Level"],as_index=False).count()

# Level別Clear数(No Fail除く)
df_cleared = df_scores[(1==1)
                &(df_scores["Modifiers"] != "NF")
                & (df_scores["Ranked"] == True)
                ][["Level","Song"]].groupby(["Level"],as_index=False).count().rename(columns={"Song": "Cleared"})

# Level別 No fail数
df_cleared_nf = df_scores[(1==1)
                &(df_scores["Modifiers"] == "NF")
                & (df_scores["Ranked"] == True)
                ][["Level","Song"]].groupby(["Level"],as_index=False).count().rename(columns={"Song": "NF"})

# 直近のLevel別Clear数(No Fail除く)
df_cleared_latest = df_scores[(1==1)
                       &(df_scores["Modifiers"] != "NF")
                       & (df_scores['Ranked'] == True)
                       & (df_scores["Latest"] == 1)
                ][["Level","Song"]].groupby(["Level"],as_index=False).count().rename(columns={"Song": "RecentCleared"})

# 結合
df_progress = pd.merge(df_progress, df_cleared_latest, on="Level", how="outer")
df_progress = pd.merge(df_progress, df_cleared, on="Level", how="outer")
df_progress = pd.merge(df_progress, df_cleared_nf, on="Level", how="outer")

df_progress["NotCleared"] = df_progress["Song"].fillna(0) - df_progress["Cleared"].fillna(0) - df_progress["NF"].fillna(0)
df_progress["AlreadyCleared"] = df_progress["Cleared"].fillna(0) - df_progress["RecentCleared"].fillna(0)
df_progress = df_progress.fillna(0)
df_progress["NotClearedRate"] = df_progress["NotCleared"] / df_progress["Song"] * 100
df_progress["AlreadyClearedRate"] = df_progress["AlreadyCleared"] / df_progress["Song"] * 100
df_progress["RecentClearedRate"] = df_progress["RecentCleared"] / df_progress["Song"] * 100
df_progress["NFRate"] = df_progress["NF"] / df_progress["Song"] * 100

# Accの内訳
df_acc =df_scores[(1==1)
                &(df_scores["Modifiers"] != "NF")
                & (df_scores['Ranked'] == True)
                ].pivot_table(index="Level", columns= "AccRank", values="Song", aggfunc="count").fillna(0).reset_index()

if ss_plus_is_enable:
    cols_accs = ["SSS",ss_plus,"S","A","B"]
else:
    cols_accs = ["SSS","SS","S","A","B"]

for cols_acc in cols_accs:
    if cols_acc in df_acc.columns :
        pass
    else:
        print("Rank{}データ無し".format(cols_acc))
        df_acc[cols_acc] = 0

# Accの結合
df_progress = pd.merge(df_progress, df_acc, on="Level", how="outer").fillna(0)
df_progress["Other"] = df_progress["Song"] - df_progress["SSS"] - df_progress["SS"] - df_progress["S"] - df_progress["A"] - df_progress["B"]
df_progress["SSS-Rate"] = df_progress["SSS"] / df_progress["Song"] * 100
if ss_plus_is_enable:
    df_progress["Other"] = df_progress["Other"] - df_progress[ss_plus]
    df_progress[ss_plus_rate] = df_progress[ss_plus] / df_progress["Song"] * 100
df_progress["SS-Rate"] = df_progress["SS"] / df_progress["Song"] * 100
df_progress["S-Rate"] = df_progress["S"] / df_progress["Song"] * 100
df_progress["A-Rate"] = df_progress["A"] / df_progress["Song"] * 100
df_progress["B-Rate"] = df_progress["B"] / df_progress["Song"] * 100
df_progress["Other-Rate"] = df_progress["Other"] / df_progress["Song"] * 100

# FCの内訳
df_fc = df_scores[(1==1)
                &(df_scores["Modifiers"] != "NF")
                & (df_scores["Ranked"] == True)
                & (df_scores["FC"] == "FC")
                ][["Level","Song"]].groupby(["Level"],as_index=False).count().rename(columns={"Song": "FC"})

df_fc_latest = df_scores[(1==1)
            &(df_scores["Modifiers"] != "NF")
            & (df_scores['Ranked'] == True)
            & (df_scores["Latest"] == 1)
            & (df_scores["FC"] == "FC")
        ][["Level","Song"]].groupby(["Level"],as_index=False).count().rename(columns={"Song": "RecentFC"})

# FCの結合
df_progress = pd.merge(df_progress, df_fc, on="Level", how="outer")
df_progress = pd.merge(df_progress, df_fc_latest, on="Level", how="outer")
df_progress["AlreadyFC"] = df_progress["FC"].fillna(0) - df_progress["RecentFC"].fillna(0)
df_progress["NotFC"] = df_progress["Cleared"].fillna(0) + df_progress["NF"].fillna(0) - df_progress["FC"].fillna(0)
df_progress = df_progress.fillna(0)
df_progress["AlreadyFCRate"] = df_progress["AlreadyFC"] / df_progress["Song"] * 100
df_progress["RecentFCRate"] = df_progress["RecentFC"] / df_progress["Song"] * 100
df_progress["NotFCRate"] = df_progress["NotFC"] / df_progress["Song"] * 100

df_progress.to_csv(level_cleared_path, index=False)

<IPython.core.display.Javascript object>

RankSSSデータ無し


In [ ]:
#@title (検算用)
ranked_count = df_progress["Song"].sum()
cleared_count = int(df_progress["Cleared"].sum())
nofail_count = int(df_progress["NF"].sum())
play_count = cleared_count + nofail_count
fc_count = int(df_progress["FC"].sum())
recent_cleared_count = int(df_progress["RecentCleared"].sum())

print("Rank譜面数:{}, Clear数:{}, NoFail数:{}, Play数:{}, FC数:{}".format(ranked_count, cleared_count, nofail_count, play_count, fc_count))

<IPython.core.display.Javascript object>

Rank譜面数:2936, Clear数:1524, NoFail数:76, Play数:1600, FC数:682


## Player情報の記録と読込(df_infos)

In [ ]:
#@title FC情報の結合とPlayer情報の記録と読込
df_info["Pic"] = '<img src="'+df_info["profilePicture"]+'"/>'
df_info["TotalScore"] = df_info["scoreStats.totalScore"]
df_info["RankedScore"] = df_info["scoreStats.totalRankedScore"]
df_info["AveRankedAcc"] = df_info["scoreStats.averageRankedAccuracy"]
df_info["TotalPlay"] = df_info["scoreStats.totalPlayCount"]
df_info["RankedPlay"] = df_info["scoreStats.rankedPlayCount"]
df_info["ReplayWatched"] = df_info["scoreStats.replaysWatched"]
df_info["ScoreDate"] = datetime.now().strftime("%Y/%m/%d %H:%M:%S")
df_info["TotalFC"] = df_scores[df_scores['FC']=='FC']['FC'].count()
df_info["RankedFC"] = df_progress["FC"].sum()
PlayCount = df_info["TotalPlay"][0]
RangeCount = math.ceil(PlayCount / page_count) + 1

df_infos = pd.read_csv(player_info_path)
df_info_csv = df_info[cols_info].copy()
# 結合とソート
df_info_csv.append(df_infos).sort_values('ScoreDate').reset_index().drop('index', axis=1)

if os.path.exists(player_info_path):
    df_infos = pd.read_csv(player_info_path)
    df_info_csv = df_info[cols_info].copy()
    # 結合とソート
    df_info_csv = df_info_csv.append(df_infos).sort_values('ScoreDate').reset_index().drop('index', axis=1)
    # df_infos = pd.read_csv(player_info_path)
    df_info_csv.to_csv(player_info_path, index=None)
    # df_info[cols_info].to_csv(player_info_path, mode="a", index=None)#, header=False)
else:
    df_info[cols_info].to_csv(player_info_path, index=None)

df_infos = pd.read_csv(player_info_path)
df_infos["ScoreDate"] = pd.to_datetime(df_infos["ScoreDate"])

print("Play数:{}, Page数:{}".format(PlayCount, RangeCount))

<IPython.core.display.Javascript object>

Play数:1639, Page数:206


# 分析 可視化

## Player Summary

In [ ]:
#@title Player Info
styles = [
    dict(selector="td", props=[("font-size", "130%"),
                               ("text-align", "center")])
]

df_info[cols_info_sort].style.set_table_styles(styles).highlight_null(null_color="lightgray").set_precision(2)


<IPython.core.display.Javascript object>

In [ ]:
#@title Player Summary
rank_yaxis_reversed_is_enable = True #@param {type:"boolean"}
since_x_days_ago = latest + 1
#param {type:"number"}
import plotly.graph_objects as go
from plotly.subplots import make_subplots

def get_summary_diff(_df_summary, _col, reversed_is_enable=False):
    _after = df_info.iloc[0][_col]
    try:
        _before = _df_summary.iloc[-1-since_x_days_ago][_col]
    except:
        _before = _after

    if reversed_is_enable:
        _diff = _before - _after
    else:
        _diff = _after - _before
    return _before, _after, _diff

df_summary = df_infos.copy()

df_summary["ScoreDateUtc"] = pd.to_datetime(df_summary['ScoreDate'], utc=True)
_df_summary_idx = df_summary.set_index("ScoreDateUtc")
df_summary["ScoreDateJa"] = _df_summary_idx.index.tz_convert("Asia/Tokyo")
df_summary = df_summary.set_index("ScoreDateJa")
df_summary = df_summary.reset_index()

df_summary_score = df_summary.set_index('ScoreDateJa').resample('1D').max().fillna(method='ffill')
df_summary_rank = df_summary.set_index('ScoreDateJa').resample('1D').min().fillna(method='ffill')

if len(df_summary_score) >= since_x_days_ago+1:
    if since_x_days_ago == 1:
        from_date = "YTD"
    else:
        from_date = "[{}]".format(df_summary_score.index[-1-since_x_days_ago].strftime('%m.%d'))
    rank_diff = get_summary_diff(df_summary_rank, 'rank', rank_yaxis_reversed_is_enable)
    country_rank_diff = get_summary_diff(df_summary_rank, 'countryRank', rank_yaxis_reversed_is_enable)
    pp_diff = get_summary_diff(df_summary_score, 'pp')
    acc_diff = get_summary_diff(df_summary_score, 'AveRankedAcc')
    total_play_diff = get_summary_diff(df_summary_score, 'TotalPlay')
    ranked_play_diff = get_summary_diff(df_summary_score, 'RankedPlay')
    total_fc_diff = get_summary_diff(df_summary_score, 'TotalFC')
    ranked_fc_diff = get_summary_diff(df_summary_score, 'RankedFC')

    fig = make_subplots(
        rows=8, cols=1,
        subplot_titles=(
            "Global Rank : {} {}->{}({:+})".format(from_date,rank_diff[0],rank_diff[1],rank_diff[2]),
            "{} Rank : {} {}->{}({:+})".format(df_info["country"][0],from_date,country_rank_diff[0],country_rank_diff[1],country_rank_diff[2]),
            "Total PP : {} {:.2f}->{:.2f}({:+.2f})".format(from_date,pp_diff[0],pp_diff[1],pp_diff[2]), 
            "Average Ranked Acc : {} {:.2f}->{:.2f}({:+.2f})".format(from_date,acc_diff[0],acc_diff[1],acc_diff[2]), 
            "Total Play Count : {} {}->{}({:+})".format(from_date,total_play_diff[0],total_play_diff[1],total_play_diff[2]), 
            "Ranked Play Count : {} {}->{}({:+})".format(from_date,ranked_play_diff[0],ranked_play_diff[1],ranked_play_diff[2]),
            "Total FC Count : {} {}->{}({:+})".format(from_date,total_fc_diff[0],total_fc_diff[1],total_fc_diff[2]), 
            "Ranked FC Count : {} {}->{}({:+})".format(from_date,ranked_fc_diff[0],ranked_fc_diff[1],ranked_fc_diff[2])
            ))
    
else:
    fig = make_subplots(
        rows=8, cols=1,
        subplot_titles=(
            "Global Rank :{}".format(df_info.iloc[0]['rank']),
            "{} Rank : {}".format(df_info["country"][0],df_info.iloc[0]['countryRank']),
            "Total PP : {:.2f}".format(df_info.iloc[0]['pp']), 
            "Average Ranked Acc : {:.2f}".format(df_info.iloc[0]['AveRankedAcc']), 
            "Total Play Count : {}".format(df_info.iloc[0]['TotalPlay']), 
            "Ranked Play Count : {}".format(df_info.iloc[0]['RankedPlay']),
            "Total FC Count : {}".format(df_info.iloc[0]['TotalFC']), 
            "Ranked FC Count : {}".format(df_info.iloc[0]['RankedFC'])
            ))

fig.add_trace(go.Scatter(x=df_summary["ScoreDateJa"], y=df_summary["rank"], name="Rank"),row=1,col=1)
fig.add_trace(go.Scatter(x=df_summary["ScoreDateJa"], y=df_summary["countryRank"], name="{}-Rank".format(df_info["country"][0])), row=2, col=1)
fig.add_trace(go.Scatter(x=df_summary["ScoreDateJa"], y=df_summary["pp"], name="PP"),row=3,col=1)
fig.add_trace(go.Scatter(x=df_summary["ScoreDateJa"], y=df_summary["AveRankedAcc"], name="Acc"),row=4,col=1)
fig.add_trace(go.Scatter(x=df_summary["ScoreDateJa"], y=df_summary["TotalPlay"], name="TotalPlay"),row=5,col=1)
fig.add_trace(go.Scatter(x=df_summary["ScoreDateJa"], y=df_summary["RankedPlay"], name="RankedPlay"),row=6,col=1)
fig.add_trace(go.Scatter(x=df_summary["ScoreDateJa"], y=df_summary["TotalFC"], name="TotalFC"),row=7,col=1)
fig.add_trace(go.Scatter(x=df_summary["ScoreDateJa"], y=df_summary["RankedFC"], name="RankedFC"),row=8,col=1)


fig.update_layout(barmode="relative", title_text="Player Summary - {} - {}".format(tz_ja.strftime("%Y.%m.%d"), df_info["name"][0]),
                  width=1000, height=1000,
                    # xaxis_rangeslider=dict(
                    #     visible=True,
                    #     #bgcolor='black',  # 背景色
                    #     #bordercolor='violet',  # 枠線の色
                    #     #borderwidth=6,  # 枠線の太さ
                    #     #thickness=0.3,  # レンジスライダーの厚さ
                    # ),
                  hovermode="x unified")


# RankのY軸反転
if rank_yaxis_reversed_is_enable:
    fig.update_layout(
        yaxis_autorange="reversed"
        ,yaxis2_autorange="reversed"
    )


fig.show()

<IPython.core.display.Javascript object>

## Ranked - Latest History / Parallel Coordinates Analysis - HiPlot (df_history)
※現在取得結果が0件の場合エラーが発生する不具合があります。  
　エラーが発生する場合はフィルターの条件を緩和して再度実行してください。  

In [ ]:
#@title ## Ranked - Latest History / Parallel Coordinates Analysis - HiPlot
filtered_level_min = 0 #@param {type:"slider", min:0, max:15, step:1}
filtered_level_max = 15 #@param {type:"slider", min:0, max:15, step:1}
filtered_pp_min = 0 #@param {type:"slider", min:0, max:600, step:10}
filtered_pp_max = 600 #@param {type:"slider", min:0, max:600, step:10}
filtered_acc_min = 0 #@param {type:"slider", min:0, max:100, step:1}
filtered_acc_max = 100 #@param {type:"slider", min:0, max:100, step:1}
default_sort_key = "PP" #@param ["PP", "DateJa"]
filtered_latest_is_enable = False #@param {type:"boolean"}
filtered_ranked_is_enable = True #@param {type:"boolean"}

df_history = df_scores[(1==1)
    & (df_scores["Modifiers"] != "NF")
    & (df_scores["Stars"] >= filtered_level_min)
    & (df_scores["Stars"] < filtered_level_max)
    & (df_scores["PP"] >= filtered_pp_min)
    & (df_scores["PP"] < filtered_pp_max)
    & (df_scores["Acc"] >= filtered_acc_min)
    & (df_scores["Acc"] <= filtered_acc_max)]

if filtered_latest_is_enable:
    df_history = df_history[(df_history["Latest"] == 1)]

if filtered_ranked_is_enable:
    df_history = df_history[(df_history['Ranked']==1)]

df_history = df_history[cols_score]

df_history = df_history.reset_index()

df_history["DateJa"] = df_history["DateJa"].astype("str")

exp = hip.Experiment.from_dataframe(df_history)

exp.display_data(hip.Displays.PARALLEL_PLOT).update({
    # Hide some columns in the parallel plot
    "hide": ["uid", "from_uid", "Song", "Cover", "DateJa", "Difficulty","Tags","Preview"],
    "colorby": ["Stars"],
    # Specify the order for others
    "order": ["PP"],  # Put column time first on the left
})

exp.display_data(hip.Displays.TABLE).update({
    # Don"t display `uid` and `from_uid` columns to the user
    "hide": ["uid", "from_uid", "Level", "Ranked", "Days", "Months"],
    # In the table, order rows by default
    "order_by": [[default_sort_key, "desc"]],
    # Specify the order for columns
    "order": ["pp"],  # Put column time first on the left
})

exp.display()
# srcdoc = exp.to_html()  # Store html as string
# HTML(srcdoc)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

## Ranked - Level Cleared Progress
データの説明については [データについての捕捉](#scrollTo=ckfQPyy2b3Gn)を、  
データの内訳については [clear情報 df_progress 内訳](#scrollTo=uiy6go_3VASb) を参照ください。

In [ ]:
#@title Ranked - Level Cleared Progress
full_combo_progress_is_enable = True #@param {type:"boolean"}
import plotly.graph_objects as go
from plotly.subplots import make_subplots

if full_combo_progress_is_enable:
    rows_count = 3
    plot_titles = ["Cleared Count", "Cleared Rate", "Acc Ranked Count", "Acc Ranked Rate", "Full Combo Count", "Full Combo Rate"]
else:
    rows_count = 2
    plot_titles = ["Cleared Count", "Cleared Rate", "Acc Ranked Count", "Acc Ranked Rate"]

fig = make_subplots(
    rows=rows_count, cols=2,
    horizontal_spacing=0.065,
    vertical_spacing=0.075,
    subplot_titles=(plot_titles)
    )

# Cleared
fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["AlreadyCleared"], name="AlreadyCleared", marker_color="#636EFA"),row=1,col=1)
fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["RecentCleared"], name="RecentCleared", marker_color="#ff4500"),row=1,col=1)
fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["NF"], name="NoFail", marker_color="#a0a0a0"),row=1,col=1)
fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["NotCleared"], name="NotCleared", marker_color="#dcdcdc"),row=1,col=1)

# Clear annotation
fig.add_annotation(x=10,y=400, xref="x", yref="y",
        text="          ",                       
        borderpad=30,bgcolor="#FFFFFF",
        font=dict(size=12,color="#00CC00"), align="center",showarrow=False, opacity=0.8,row=1,col=1
        )

fig.add_annotation(
        x=10,y=450, xref="x", yref="y",
        text="Songs:{}".format(int(df_progress["Song"].sum())),
        font=dict(size=12,color="#333333"),
        align="center",showarrow=False, opacity=0.8
        ,row=1,col=1
        )

fig.add_annotation(
        x=10,y=400, xref="x", yref="y",
        text="Cleared:{}".format(int(df_progress["Cleared"].sum())),
        font=dict(size=12,color="#636EFA"),
        align="center",showarrow=False, opacity=0.8
        ,row=1,col=1
        )

fig.add_annotation(
        x=10,y=350, xref="x", yref="y",
        text="(Recent:{})".format(int(df_progress["RecentCleared"].sum())),
        font=dict(size=12,color="#ff4500"),
        align="center",showarrow=False, opacity=0.8
        ,row=1,col=1
        )

fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["AlreadyClearedRate"], name="AlreadyClearedRate", marker_color="#636EFA"),row=1,col=2)
fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["RecentClearedRate"], name="RecentClearedRate", marker_color="#ff4500"),row=1,col=2)
fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["NFRate"], name="NoFailRate", marker_color="#a0a0a0"),row=1,col=2)
fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["NotClearedRate"], name="NotClearedRate",marker_color="#dcdcdc"),row=1,col=2)

# Acc Rank
fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["SSS"], name="SSS", marker_color="#00ffff"),row=2,col=1)
if ss_plus_is_enable:
    fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress[ss_plus], name=ss_plus, marker_color="#636EFA"),row=2,col=1)
fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["SS"], name="SS", marker_color="#ff4500"),row=2,col=1)
fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["S"], name="S", marker_color="#ffaaff"),row=2,col=1)
fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["A"], name="A", marker_color="#ffcc66"),row=2,col=1)
fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["B"], name="B", marker_color="#fffd88"),row=2,col=1)
fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["Other"], name="Other",marker_color="#dcdcdc"),row=2,col=1)

fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["SSS-Rate"], name="SSS-Rate", marker_color="#00ffff"),row=2,col=2)
if ss_plus_is_enable:
    fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress[ss_plus_rate], name=ss_plus_rate, marker_color="#636EFA"),row=2,col=2)
fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["SS-Rate"], name="SS-Rate", marker_color="#ff4500"),row=2,col=2)
fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["S-Rate"], name="S-Rate", marker_color="#ffaaff"),row=2,col=2)
fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["A-Rate"], name="A-Rate", marker_color="#ffcc66"),row=2,col=2)
fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["B-Rate"], name="B-Rate", marker_color="#fffd88"),row=2,col=2)
fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["Other-Rate"], name="Other-Rate",marker_color="#dcdcdc"),row=2,col=2)

# Acc annotation
fig.add_annotation(x=10,y=375, xref="x", yref="y",
        text="  ",                       
        borderpad=45,bgcolor="#FFFFFF",
        font=dict(size=12,color="#00CC00"), align="center",showarrow=False, opacity=0.8,row=2,col=1
        )

if ss_plus_is_enable:
    fig.add_annotation(x=10,y=500, xref="x", yref="y",
            text="SSS:{}".format(int(df_progress["SSS"].sum())),
            font=dict(size=12,color="#00DDDD"), align="center",showarrow=False, opacity=0.8, row=2,col=1
            )

    fig.add_annotation(x=10,y=450, xref="x", yref="y",
            text="{}:{}".format(ss_plus,int(df_progress[ss_plus].sum())),
            font=dict(size=12,color="#636EFA"),align="center",showarrow=False, opacity=0.8, row=2,col=1
            )
else:
    fig.add_annotation(x=10,y=450, xref="x", yref="y",
        text="SSS:{}".format(int(df_progress["SSS"].sum())),
        font=dict(size=12,color="#00DDDD"), align="center",showarrow=False, opacity=0.8, row=2,col=1
        )

fig.add_annotation(x=10,y=400, xref="x", yref="y",
        text="SS:{}".format(int(df_progress["SS"].sum())),
        font=dict(size=12,color="#ff4500"),align="center",showarrow=False, opacity=0.8,row=2,col=1
        )

fig.add_annotation(x=10,y=350, xref="x", yref="y",
        text="S:{}".format(int(df_progress["S"].sum())),
        font=dict(size=12,color="#ffaaff"),align="center",showarrow=False, opacity=0.8,row=2,col=1
        )

fig.add_annotation(x=10,y=300, xref="x", yref="y",
        text="A:{}".format(int(df_progress["A"].sum())),
        font=dict(size=12,color="#ffbb55"),align="center",showarrow=False, opacity=0.8,row=2,col=1
        )

fig.add_annotation(x=10,y=250, xref="x", yref="y",
        text="B:{}".format(int(df_progress["B"].sum())),
        font=dict(size=12,color="#ffed66"),align="center",showarrow=False, opacity=0.8,row=2,col=1
        )

# Full Combo
if full_combo_progress_is_enable:
    # fc plot
    fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["AlreadyFC"], name="AlreadyFC", marker_color="#00eecc"),row=3,col=1)
    fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["RecentFC"], name="RecentFC", marker_color="#ff4500"),row=3,col=1)
    fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["NotFC"], name="NotFC", marker_color="#a0a0a0"),row=3,col=1)
    fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["NotCleared"], name="NotCleared", marker_color="#dcdcdc"),row=3,col=1)

    # fc rate plot
    fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["AlreadyFCRate"], name="AlreadyFCRate", marker_color="#00eecc"),row=3,col=2)
    fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["RecentFCRate"], name="RecentFCRate", marker_color="#ff4500"),row=3,col=2)
    fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["NotFCRate"], name="NotFCRate", marker_color="#a0a0a0"),row=3,col=2)
    fig.add_trace(go.Bar(x=df_progress["Level"], y=df_progress["NotClearedRate"], name="NotClearedRate",marker_color="#dcdcdc"),row=3,col=2)

    fig.add_annotation(x=10,y=400, xref="x", yref="y",
            text="          ",                       
            borderpad=30,bgcolor="#FFFFFF",
            font=dict(size=12,color="#00CC00"), align="center",showarrow=False, opacity=0.8,row=3,col=1
            )

    fig.add_annotation(x=10,y=450, xref="x", yref="y",
            text="Songs:{}".format(int(df_progress["Song"].sum())),
            font=dict(size=12,color="#333333"), align="center",showarrow=False, opacity=0.8 ,row=3,col=1
            )

    fig.add_annotation(x=10,y=400, xref="x", yref="y",
            text="FC:{}".format(int(df_progress["FC"].sum())),
            #borderpad=30,bgcolor="#FFFFFF",
            font=dict(size=12,color="#00CC00"), align="center",showarrow=False, opacity=0.8,row=3,col=1
            )

    fig.add_annotation(x=10,y=350, xref="x", yref="y",
            text="(Recent:{})".format(int(df_progress["RecentFC"].sum())),
            font=dict(size=12,color="#ff4500"),align="center",showarrow=False, opacity=0.8, row=3,col=1
            )

fig.update_layout(barmode="relative", title_text="Ranked - Level Cleared Progress - {} - {}".format(tz_ja.strftime("%Y.%m.%d"), df_info["name"][0]),width=1000, height=800)
fig.show()

<IPython.core.display.Javascript object>

In [ ]:
#@title Level Cleared Progress 内訳(df_progress)
view_filter = "RecentClear&FC" #@param ["Clear&FC", "Acc","Clear&FC&Acc","RecentClear&FC" ,"All"]
ranked_count = df_progress["Song"].sum()
cleared_count = int(df_progress["Cleared"].sum())
nofail_count = int(df_progress["NF"].sum())
play_count = cleared_count + nofail_count
fc_count = int(df_progress["FC"].sum())
recent_cleared_count = int(df_progress["RecentCleared"].sum())

# 表示
if view_filter == "Clear&FC":
    cols_view = ["Song", "Cleared", "FC"]
elif view_filter == "Acc":
    if ss_plus_is_enable:
        cols_view = ["Song", "SSS", ss_plus, "SS", "S", "A", "B"]
    else:
        cols_view = ["Song", "SSS", "SS", "S", "A", "B"]

elif view_filter == "Clear&FC&Acc":
    if ss_plus_is_enable:
        cols_view = ["Song", "Cleared", "FC", "SSS", ss_plus, "SS", "S", "A", "B"]
    else:
        cols_view = ["Song", "Cleared", "FC", "SSS", "SS", "S", "A", "B"]
elif view_filter == "RecentClear&FC":
    cols_view = ["Song", "Cleared", "RecentCleared", "FC", "RecentFC"]
else:
    cols_view = df_progress.columns.values.tolist()
    cols_view.remove('Level')

def append_sum_row(df):
    return df.append(df.sum(numeric_only=True), ignore_index=True)

def append_sum_row_label(df):
    df.loc['Total'] = df.sum(numeric_only=True)
    return df

_df_progress = df_progress.copy()
_df_progress = _df_progress.set_index('Level')

df_progress_total = append_sum_row_label(_df_progress)

df_progress_total[cols_view].style.highlight_null(null_color="lightgray").set_precision(0)

<IPython.core.display.Javascript object>

## Ranked - ScatterPlot Analysis

In [ ]:
#@title Ranked - ScatterPlot Analysis
import plotly.io as pio
def show_plot(col_x, col_y, size, color, pp_min, pp_max, star_min, star_max, latest):

    def _func_latest(x):
        if  x <= latest:
            return "latest {}day".format(latest)
        else:
            return "old".format(latest)

    df_scores["LatestStr"] = df_scores["Days"].apply(_func_latest).astype("str")
      
    fig2 = px.scatter(df_scores[(df_scores['Ranked']==1)
                       & (df_scores["PP"] >= pp_min)
                       & (df_scores["PP"] <= pp_max)
                       & (df_scores["Stars"] >= star_min)
                       & (df_scores["Stars"] <= star_max)
                                                 #& (df_scores["Months"] <= 1)
                        ], x=col_x, y=col_y, color=color,
                     #animation_frame="MonthsStr", #animation_group="country",
                     size=size, hover_data=["PP","Acc","AccRank","Score","Miss","Bad","Song"],
                     width=800, height=800)

    fig2.update_layout(title="Ranked - ScatterPlot Analysis - {} - {}".format(tz_ja.strftime("%Y.%m.%d"), df_info["name"][0]), title_x=0.5,
                  xaxis_title = "x:{} (markersize:{}, markercolor:{})".format(col_x, size, color), yaxis_title="y:{}".format(col_y)
                  )
                  #font=dict(family="Times",size=18,color="black"))

    fig2.show()

w1 = ToggleButtons(description="X軸:", options=cols_xy)
w2 = ToggleButtons(description="Y軸:", options=cols_xy)
w3 = ToggleButtons(description="Size:", options=cols_xy)
w4 = ToggleButtons(description="Color:", options=cols_cate)

slider_star_min = IntSlider(
    value=0,
    min=0,
    max=15,
    step=1,
    description="Star min:"
)

slider_star_max = IntSlider(
    value=15,
    min=0,
    max=15,
    step=1,
    description="Star max:"
)

slider_pp_min = IntSlider(
    value=0,
    min=0,
    max=600,
    step=10,
    description="PP min:"
)

slider_pp_max = IntSlider(
    value=600,
    min=0,
    max=600,
    step=10,
    description="PP max:"
)

slider_latest = IntSlider(
    value=-1,
    min=-1,
    max=365,
    step=1,
    description="LatestFilter:"
)

interact(show_plot, col_x=w1, col_y=w2, size=w3, color=w4, pp_min=slider_pp_min, pp_max=slider_pp_max, star_min=slider_star_min, star_max=slider_star_max, latest=slider_latest)

<IPython.core.display.Javascript object>

interactive(children=(ToggleButtons(description='X軸:', options=('Stars', 'Level', 'Acc', 'Rank', 'PP', 'Miss',…

<function __main__.show_plot>

## Ranked - Worst/Top Score Analysis (df_worst, df_top, df_worst_top)
・各項目は条件を絞ったのち Levelごとにworst_count(top_count)分の結果を取得します。

In [ ]:
#@title Worst Scores (Playlist Download)
filtered_level_min = 0 #@param {type:"slider", min:0, max:15, step:1}
filtered_level_max = 15 #@param {type:"slider", min:0, max:15, step:1}
filtered_pp_min = 0 #@param {type:"slider", min:0, max:600, step:10}
filtered_pp_max = 600 #@param {type:"slider", min:0, max:600, step:10}
filtered_acc_min = 0 #@param {type:"slider", min:0, max:100, step:1}
filtered_acc_max = 100 #@param {type:"slider", min:0, max:100, step:1}
filtered_miss_min = 0 #@param {type:"number"}
filtered_miss_max = 5000 #@param {type:"number"}
worst_target = "PP" #@param ["Acc", "PP"]
worst_count =  3#@param {type:"number"}
not_fullcombo_filter_is_enable = True #@param {type:"boolean"}
# playlistの出力
download_playlist_is_enable = True #@param {type:"boolean"}

df_worst = df_scores.head(0)
df_filtered = df_scores[(1==1)
    & (df_scores["Ranked"]==1)
    & (df_scores["Stars"] >= filtered_level_min)
    & (df_scores["Stars"] <= filtered_level_max)
    & (df_scores["PP"] >= filtered_pp_min)
    & (df_scores["PP"] <= filtered_pp_max)
    & (df_scores["Acc"] >= filtered_acc_min)
    & (df_scores["Acc"] <= filtered_acc_max)
    & (df_scores["Miss"] + df_scores["Bad"] >= filtered_miss_min)
    & (df_scores["Miss"] + df_scores["Bad"] <= filtered_miss_max)
]

if not_fullcombo_filter_is_enable:
    df_filtered = df_filtered[df_filtered['FC'] != "FC"]

for level in range(filtered_level_min, filtered_level_max):
    df_worst = df_worst.append(df_filtered[df_filtered["Level"]==level].sort_values(worst_target).head(worst_count))#, ignore_index=True)


if download_playlist_is_enable:

    # playlistの出力
    songs = []
    for i, x in df_worst.iterrows():
        songs += [{
            "songName": x["SongName"],
            "levelAuthorName": x["LevelAuthor"],
            "hash": x["Hash"],
            "levelid": f"custom_level_{x['Hash']}",
            "difficulties": [
                {
                    "characteristic": "Standard",
                    "name": x["Difficulty"]
                }
            ]
        }]
    #} for x in df_playlist.iterrows]

    playlist = {
        "playlistTitle": "{}_WorstScores".format(tz_ja.strftime("%Y.%m.%d")),
        "playlistAuthor": "hatopop",
        "songs": songs
        #,"image": img
    }

    # song_worst_playlist_path = r"{}/worst_playlist_{}.json".format(data_path, datetime.now().strftime("%Y%m%d"))

    with open(song_worst_playlist_path, "w") as f:
        json.dump(playlist, f)

        files.download(song_worst_playlist_path)

    print("Level {}-{}, Worst{} Playlistを出力しました. 曲数:{}.".format(filtered_level_min, filtered_level_max, worst_count, df_worst["Play"].count()))

df_worst["WorstTop"] = "Worst" 

df_worst[cols_score].sort_values(["Level","Acc"]).style.highlight_null(null_color="lightgray").set_precision(2)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Level 0-15, Worst3 Playlistを出力しました. 曲数:31.


In [ ]:
#@title Top Scores (Playlist Download)
filtered_level_min = 0 #@param {type:"slider", min:0, max:15, step:1}
filtered_level_max = 15 #@param {type:"slider", min:0, max:15, step:1}
filtered_pp_min = 0 #@param {type:"slider", min:0, max:600, step:10}
filtered_pp_max = 600 #@param {type:"slider", min:0, max:600, step:10}
filtered_acc_min = 0 #@param {type:"slider", min:0, max:100, step:1}
filtered_acc_max = 100 #@param {type:"slider", min:0, max:100, step:1}
filtered_miss_min =  0#@param {type:"number"}
filtered_miss_max = 5000 #@param {type:"number"}
top_target = "PP" #@param ["Acc", "PP"]
top_count =  3#@param {type:"number"}
not_fullcombo_filter_is_enable = True #@param {type:"boolean"}
#@title playlistの出力
download_playlist_isenable = True #@param {type:"boolean"}


df_top = df_scores.head(0)
df_filtered = df_scores[(1==1)
    & (df_scores['Ranked']==1)
    & (df_scores["Stars"] >= filtered_level_min)
    & (df_scores["Stars"] <= filtered_level_max)
    & (df_scores["PP"] >= filtered_pp_min)
    & (df_scores["PP"] <= filtered_pp_max)
    & (df_scores["Acc"] >= filtered_acc_min)
    & (df_scores["Acc"] <= filtered_acc_max)
    & (df_scores["Miss"] + df_scores["Bad"] >= filtered_miss_min)
    & (df_scores["Miss"] + df_scores["Bad"] <= filtered_miss_max)
]

if not_fullcombo_filter_is_enable:
    df_filtered = df_filtered[df_filtered['FC'] != "FC"]

for level in range(filtered_level_min, filtered_level_max):
    df_top = df_top.append(df_filtered[df_filtered["Level"]==level].sort_values(top_target, ascending=False).head(top_count))#, ignore_index=True)


if download_playlist_isenable:

    # playlistの出力
    songs = []
    for i, x in df_top.iterrows():
        songs += [{
            "songName": x["SongName"],
            "levelAuthorName": x["LevelAuthor"],
            "hash": x["Hash"],
            "levelid": f"custom_level_{x['Hash']}",
            "difficulties": [
                {
                    "characteristic": "Standard",
                    "name": x["Difficulty"]
                }
            ]
        }]
    #} for x in df_playlist.iterrows]

    playlist = {
        "playlistTitle": "{}_TopScores".format(tz_ja.strftime("%Y.%m.%d")),
        "playlistAuthor": "hatopop",
        "songs": songs
        #,"image": img
    }

    # song_top_playlist_path = r"{}/top_playlist_{}.json".format(data_path, datetime.now().strftime("%Y%m%d"))

    with open(song_top_playlist_path, "w") as f:
        json.dump(playlist, f)

        files.download(song_top_playlist_path)

    print("Level {}-{}, Top{} Playlistを出力しました. 曲数:{}.".format(filtered_level_min, filtered_level_max, top_count, df_top["Play"].count()))

df_top["WorstTop"] = "Top" 

df_top[cols_score].sort_values(["Level","Acc"]).style.highlight_null(null_color="lightgray").set_precision(2)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Level 0-15, Top3 Playlistを出力しました. 曲数:31.


In [ ]:
#@title WorstとTop結合
df_worst_top = df_worst
df_worst_top = df_worst_top.append(df_top)#filtered[df_filtered["Level"]==level].sort_values("Acc", ascending=False).head(top_count))#, ignore_index=True)

<IPython.core.display.Javascript object>

In [ ]:
#@title Worst/Top ScatterPlot Analysis
def show_plot(col_x, col_y, size, color):
    
    fig = px.scatter(df_worst_top
                        , x=col_x, y=col_y, color=color,
                     size=size, hover_data=["PP","Acc","AccRank","Score","Miss","Bad","Song"],
                     width=800, height=800)

    fig.update_layout(title="Ranked - Worst/Top - ScatterPlot Analysis - {} - {}".format(tz_ja.strftime("%Y.%m.%d"), df_info["name"][0]), title_x=0.5,
                  xaxis_title = "x:{} (markersize:{}, markercolor:{})".format(col_x, size, color), yaxis_title="y:{}".format(col_y)
                  )
                  #font=dict(family="Times",size=18,color="black"))

    fig.show()

w1 = ToggleButtons(description="X軸:", options=cols_xy)
w2 = ToggleButtons(description="Y軸:", options=cols_xy)
w3 = ToggleButtons(description="Size:", options=cols_xy)
w4 = ToggleButtons(description="Color:", options=cols_cate_wt)

interact(show_plot, col_x=w1, col_y=w2, size=w3, color=w4)

<IPython.core.display.Javascript object>

interactive(children=(ToggleButtons(description='X軸:', options=('Stars', 'Level', 'Acc', 'Rank', 'PP', 'Miss',…

<function __main__.show_plot>